In [320]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from tqdm import tqdm

plotly_margin = dict(l=0, r=0, t=0, b=0)

Обзор датасета

In [323]:
df_in = pd.read_csv("data.csv")
df_in.describe()

FileNotFoundError: [Errno 2] No such file or directory: 'lab3/data.csv'

In [332]:
corr = df_in.corr()
corr[(np.abs(corr)<0.6) | (corr == 1)] = 0
px.imshow(corr, color_continuous_scale="Picnic")

Проверим на отсутствующие значения

In [324]:
df_in.isna().any()

longitude             False
latitude              False
housing_median_age    False
total_rooms           False
total_bedrooms        False
population            False
households            False
median_income         False
median_house_value    False
dtype: bool

Геопространственное распределение цены

In [236]:
fig = go.Figure(data=go.Scattergeo(
    lat=df_in.latitude,
    lon=df_in.longitude,
    mode='markers',
    marker=dict(
        size=3,
        opacity=0.8,
        reversescale=False,
        autocolorscale=False,
        colorscale='Electric',
        color=df_in['median_house_value'],
    )
))
fig.update_layout(geo_scope='usa', margin=plotly_margin)

In [105]:
def describe_distribution(input_data):
    fig = make_subplots(7,1)
    for i, name in enumerate(["total_rooms", "total_bedrooms", "population", "households", "housing_median_age", "median_income", "median_house_value"]):
        fig.add_trace(
            go.Box(x=input_data[name], name=name, orientation='h'),
            row=1+i, col=1
        )
    
    fig.update_layout(margin=plotly_margin, height=1000, width=1600)
    fig.show()

Распределения остальных параметров

In [116]:
describe_distribution(df_in)

Можно видеть, что есть выбросы, удалим их
В таблице ниже относительное количество выбросов в %

In [126]:
q1, q3 = df_in.quantile([0.25, 0.75]).iloc
iqr = q3 - q1
lower, upper = q1 - iqr * 1.5, q3 + iqr * 1.5

df_valid = (df_in >= lower) & (df_in <= upper)
df_valid_rows = df_valid.all(axis=1)
df = df_in[df_valid_rows]

100 * (df_valid.count() - df_valid.sum()) / df_valid.count()

longitude             0.000000
latitude              0.000000
housing_median_age    0.000000
total_rooms           6.329412
total_bedrooms        6.317647
population            5.970588
households            6.070588
median_income         3.311765
median_house_value    5.264706
dtype: float64

Нормализуем данные

In [129]:
df_n = (df - df.min()) / (df.max() - df.min())

Введем синтетический признак

Немного математически некачественная, но все же оценка расстояния от моря

In [210]:
lat = df_n['latitude']
tmp_x = (lat - lat.min()) / (lat.max() - lat.min())
lon = df_n['longitude']
tmp_y = (lon - lon.min()) / (lon.max() - lon.min())

p1, p2 = [0, 0.6], [0.6, 0]
lx, ly = [p1[0], p2[0]], [p1[1], p2[1]]

# from wikipedia :)
sea_dist = np.abs((ly[1] - ly[0]) * tmp_x - (lx[1] - lx[0]) * tmp_y + lx[1] * ly[0] - ly[1] * lx[0]) 
sea_dist /= np.sqrt((ly[1] - ly[0]) ** 2 + (lx[1] - lx[0]) ** 2)
sea_dist = (sea_dist.max() - sea_dist) / sea_dist.max()
df_n['sea_dist'] = sea_dist

In [209]:
fig = px.scatter(x=tmp_x, y=tmp_y, color=sea_dist)
fig.add_trace(go.Line(x=lx, y=ly))

fig.update_layout(margin=plotly_margin)

/home/petr/.cache/pypoetry/virtualenvs/lab3-b2STYM62-py3.11/lib/python3.11/site-packages/plotly/graph_objs/_deprecations.py:378: DeprecationWarning:

plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.




Разделим тренировочную и тестовую выборку

In [211]:
train_size = 0.7
df_train = df_n.sample(frac=train_size, random_state=42)
df_test = df_n.drop(df_train.index)

print(df_train.shape, df_test.shape)

(10133, 10) (4343, 10)


Определим функции метрик

In [282]:
def loss_y(y_res, y):
    return ((y_res - y) ** 2).sum() / y.shape[0]

def loss_f(x, w, y):
    return loss_y(x.dot(w), y)

def loss_grad(x, err):
    return 2 / x.shape[0] * x.T.dot(err)

def r2(predict, test):
    return 1 - (((test - predict) ** 2).sum() / ((test - test.mean()) ** 2).sum())

Градиентный спуск

In [305]:
def add_bias_param(x):
    return np.c_[x, np.ones((x.shape[0],))]

def apply(x, w):
    return add_bias_param(x).dot(w)

def search(x, y, epochs=100, alpha=0.01, cutoff=None):
    loss_log = []
    
    w = np.random.normal(size=(x.shape[1]+1,))
    x = add_bias_param(x)
    
    if cutoff:
        epochs = 10000
    for _ in tqdm(range(epochs)):
        err = x.dot(w) - y
        w -= loss_grad(x, err) * alpha

        loss = loss_f(x, w, y)
        loss_log.append(loss)
        if cutoff and abs(loss) < cutoff:
            break

    return w, loss, loss_log

In [306]:
def select(d, params):
    return d[params], d.median_house_value


def execute(params, search_args={}, show=False):
    print("\n\nUsing params:", params)
    
    trainX, trainY = select(df_train, params)
    testX, testY = select(df_test, params)

    weight, train_loss, loss_log = search(trainX, trainY, **search_args)
    test_loss = loss_y(apply(testX, weight), testY)
    
    train_r2, test_r2 = r2(apply(trainX, weight), trainY), r2(apply(testX, weight), testY)

    if show:
        px.line(loss_log).show()

    print(f"{train_loss=:.3f}, {test_loss=:.3f}")
    print(f"{train_r2=:.3f}, {test_r2=:.3f}")

In [307]:
all_params = ["longitude", "latitude", "housing_median_age", "total_rooms", "total_bedrooms", "population", "households", "median_income"]

In [308]:
execute(all_params, dict(epochs=1000, alpha=0.1), show=True)



Using params: ['longitude', 'latitude', 'housing_median_age', 'total_rooms', 'total_bedrooms', 'population', 'households', 'median_income']


100%|██████████| 1000/1000 [00:00<00:00, 2337.99it/s]


train_loss=0.018, test_loss=0.018
train_r2=0.566, test_r2=0.557


In [311]:
execute(["latitude", "longitude"], dict(epochs=1000, cutoff=0.02, alpha=0.01))



Using params: ['latitude', 'longitude']


100%|██████████| 10000/10000 [00:03<00:00, 2656.71it/s]

train_loss=0.031, test_loss=0.031
train_r2=0.238, test_r2=0.239


In [315]:
execute(["population", "median_income", "housing_median_age"], dict(epochs=1000, cutoff=0.02, alpha=0.01))



Using params: ['population', 'median_income', 'housing_median_age']


100%|██████████| 10000/10000 [00:03<00:00, 2934.58it/s]

train_loss=0.022, test_loss=0.023
train_r2=0.449, test_r2=0.430


In [314]:
execute(["sea_dist"], dict(epochs=1000, cutoff=0.02, alpha=0.001))
execute(["median_income"], dict(epochs=1000, cutoff=0.02, alpha=0.01))
execute(["sea_dist", "median_income"], dict(epochs=1000, cutoff=0.02, alpha=0.01))



Using params: ['sea_dist']


100%|██████████| 10000/10000 [00:03<00:00, 2809.01it/s]


train_loss=0.031, test_loss=0.031
train_r2=0.246, test_r2=0.248


Using params: ['median_income']


100%|██████████| 10000/10000 [00:03<00:00, 2870.43it/s]


train_loss=0.024, test_loss=0.025
train_r2=0.407, test_r2=0.388


Using params: ['sea_dist', 'median_income']


 47%|████▋     | 4711/10000 [00:01<00:01, 2831.86it/s]

train_loss=0.020, test_loss=0.021
train_r2=0.506, test_r2=0.489
